# 3D File to Lego

First create 3D file using something like InstantMesh. Then we turn the 3D file into Lego build.

## Install Dependencies

In [ ]:
%%capture
!pip install trimesh rtree PyQt5 colormath # xformers==0.0.22.post7 rembg

## Load a 3D object

And display our mesh

In [ ]:
import trimesh
import numpy as np

mesh = trimesh.load('doll.obj')
mesh.show()

## Voxelize

We can then voxelize using a custom resolution.

In [3]:
def voxelize(mesh, resolution: int = 64):
  bounds = mesh.bounds
  voxel_size = (bounds[1] - bounds[0]).max() / 64  # pitch

  return mesh.voxelized(pitch=voxel_size)

def display_scene(mesh, voxels):
  voxels_mesh = voxels.as_boxes().apply_translation((1.5,0,0))
  scene = trimesh.Scene([mesh, voxels_mesh])

  return scene.show()

In [ ]:
voxels = voxelize(mesh)

display_scene(mesh, voxels)

## Voxelize with Color

We need to colorize voxels by fetching the N nearest colors and taking the mean.

In [127]:
import plotly.graph_objects as go
import plotly.express as px
import polars as pl

def display_voxels_px(voxels, colors):
  # Convert occupied_voxel_indices to a Polars DataFrame (if not already done)
  df = pl.from_numpy(voxels.sparse_indices, schema=["x", "y", "z"])
  df = df.with_columns(color=pl.Series(colors))
  px.scatter_3d(df, x="x", y="y", z="z", color="color",
                color_discrete_map="identity", symbol=["square"]*len(df), symbol_map="identity"
).show()

In [128]:
from scipy.spatial import cKDTree
import numpy as np

def tree_knearest_colors(k: int, mesh, voxels):
  tree = cKDTree(mesh.vertices)
  distances, vertex_indices = tree.query(voxels.points, k=k)
  voxel_colors = []

  for nearest_indices in vertex_indices:
      neighbor_colors = mesh.visual.vertex_colors[nearest_indices]
      average_color = np.mean(neighbor_colors, axis=0).astype(np.uint8)
      voxel_colors.append(average_color)

  return voxel_colors

def tree_knearest_color_mesh(k: int, mesh, voxels):
  tree = cKDTree(mesh.vertices)
  distances, vertex_indices = tree.query(voxels.points, k=k)
  voxel_colors = []

  for nearest_indices in vertex_indices:
      neighbor_colors = mesh.visual.vertex_colors[nearest_indices]
      average_color = np.mean(neighbor_colors, axis=0).astype(np.uint8)
      voxel_colors.append(average_color)

  # 2. Create a (X, Y, Z, 4) color matrix
  color_matrix = np.zeros(voxels.shape + (4,), dtype=np.uint8)  # Initialize with default color (e.g., transparent black)
  color_matrix[voxels.sparse_indices[:, 0], voxels.sparse_indices[:, 1], voxels.sparse_indices[:, 2]] = voxel_colors

  # 3. Create a VoxelMesh using as_boxes() with the color matrix
  voxel_mesh = voxels.as_boxes(colors=color_matrix)
  return voxel_mesh

### Display using scatter3d

In [ ]:
colors = tree_knearest_colors(5, mesh, voxels)
display_voxels_px(voxels, [f"rgb{c[0],c[1],c[2]}" for c in colors])

### Display using Blocks in Plotly

In [ ]:
import plotly.graph_objects as go
import numpy as np

# Assuming you have 'voxel_grid', 'colors_blocks', and 'voxels' from your previous code

# Create Mesh3d traces for each occupied voxel
mesh_data = []
for i in range(voxels.sparse_indices.shape[0]):
    x, y, z = voxels.sparse_indices[i]
    color = colors[i]  # Get color from colors_blocks
    vertices = np.array([
        [x, y, z], [x + 1, y, z], [x + 1, y + 1, z], [x, y + 1, z],
        [x, y, z + 1], [x + 1, y, z + 1], [x + 1, y + 1, z + 1], [x, y + 1, z + 1]
    ])
    faces = np.array([
        [0, 1, 2], [0, 2, 3],  # Bottom face
        [4, 5, 6], [4, 6, 7],  # Top face
        [0, 1, 5], [0, 5, 4],  # Front face
        [2, 3, 7], [2, 7, 6],  # Back face
        [0, 3, 7], [0, 7, 4],  # Left face
        [1, 2, 6], [1, 6, 5]   # Right face
    ])
    mesh_data.append(go.Mesh3d(
        x=vertices[:, 0],
        y=vertices[:, 1],
        z=vertices[:, 2],
        i=faces[:, 0],
        j=faces[:, 1],
        k=faces[:, 2],
        color=f'rgb({color[0]}, {color[1]}, {color[2]})',  # Convert to rgb string
        flatshading=True
    ))

# Create Plotly figure
fig = go.Figure(data=mesh_data)
fig.show(renderer="colab")

## Routing Algorithm 'Merge Blocks'

We need to merge blocks into LEGO pieces. Similar colors by threshold merges into uniblock. Prefer large?

In [131]:
LEGO_COLORS_RGB = np.asarray([
    (239, 239, 239),  # White
    (165, 165, 165),  # Light Bluish Gray
    (155, 155, 155),  # Light Gray
    (109, 110, 109),  # Dark Bluish Gray
    (88, 88, 88),    # Dark Gray
    (48, 48, 48),    # Black
    (196, 40, 28),   # Red
    (214, 0, 0),     # Bright Red
    (128, 0, 0),     # Dark Red
    (0, 85, 191),    # Blue
    (0, 51, 204),    # Bright Blue
    (0, 32, 96),     # Dark Blue
    (35, 122, 33),   # Green
    (0, 153, 0),     # Bright Green
    (0, 77, 0),      # Dark Green
    (247, 205, 24),  # Yellow
    (255, 204, 0),   # Bright Yellow
    (255, 153, 0),   # Dark Yellow
    (255, 102, 0),   # Orange
    (255, 128, 0),   # Bright Orange
    (124, 72, 36),   # Brown
    (160, 96, 53),   # Light Brown
    (215, 194, 149),  # Tan
    (144, 118, 72),   # Dark Tan
    (167, 205, 36),  # Lime
    (242, 176, 61),  # Bright Light Orange
    (247, 234, 142), # Bright Light Yellow
    (115, 150, 200), # Medium Blue
    (65, 165, 222),  # Medium Azure
    (137, 200, 240), # Light Azure
    (144, 31, 118),  # Magenta
    (255, 153, 204), # Pink
    (255, 189, 216)  # Light Pink
])

In [194]:
from scipy.spatial.distance import cdist
from sklearn.cluster import KMeans
from scipy.spatial import cKDTree
from colormath.color_objects import sRGBColor, LabColor
from colormath.color_conversions import convert_color
from colormath.color_diff import delta_e_cie1976

def map_colors_to_lego(model_colors, lego_palette):
  """
  cdist is optimized broadcast OP.
  """
  distances = cdist(model_colors, lego_palette, 'euclidean')  # Calculate Euclidean distances
  closest_indices = np.argmin(distances, axis=1)  # Find indices of minimum distances
  return lego_palette[closest_indices]


def convert_colors_max_diff(original_colors, predefined_colors):
    """
    Converts colors by minimizing the maximum channel difference.

    Args:
        original_colors: A NumPy array of shape (N, 3) representing original RGB colors.
        predefined_colors: A NumPy array of shape (M, 3) representing predefined RGB colors.

    Returns:
        A NumPy array of shape (N, 3) representing converted RGB colors.
    """
    diffs = np.abs(original_colors[:, np.newaxis, :] - predefined_colors)
    max_diffs = np.max(diffs, axis=2)
    indices = np.argmin(max_diffs, axis=1)

    converted_colors = predefined_colors[indices]

    return converted_colors

def quantize_colors(model_colors, k: int = 16):
  """
  quantize colors by fitting into 16 unique colors.
  """
  original_colors = np.array(colors)[:,:3]

  kmeans = KMeans(n_clusters=k, random_state=42)
  kmeans.fit(original_colors)

  # Get the representative colors
  representative_colors = kmeans.cluster_centers_.astype(int)

  # Transform the original colors to representative colors
  transformed_colors = representative_colors[kmeans.labels_]
  return transformed_colors


def map_color_cie(model_colors, lego_palette):
  original_lab = np.array([convert_color(sRGBColor(*rgb, is_upscaled=True), LabColor).get_value_tuple()
                             for rgb in model_colors])
  predefined_lab = np.array([convert_color(sRGBColor(*rgb, is_upscaled=True), LabColor).get_value_tuple()
                            for rgb in lego_palette])

  original_lab = original_lab[:, np.newaxis, :]  # Reshape for broadcasting
  predefined_lab = predefined_lab[np.newaxis, :, :]  # Reshape for broadcasting
  delta_e = np.sqrt(np.sum((original_lab - predefined_lab)**2, axis=2))

  # Find closest predefined color for each original color
  indices = np.argmin(delta_e, axis=1)

  # Transform colors
  transformed_colors = lego_palette[indices]

  return transformed_colors


def normalize_value_to_mid(rgb, target_v=0.7):
  import colorsys
  r, g, b, _ = rgb
  # Scale to [0..1]
  rr, gg, bb = (r/255, g/255, b/255)
  h, s, v = colorsys.rgb_to_hsv(rr, gg, bb)
  # Force to target_v
  rr2, gg2, bb2 = colorsys.hsv_to_rgb(h, s, target_v)
  # Scale back to [0..255]
  return (int(rr2*255), int(gg2*255), int(bb2*255))


def lab_color_tfm(colors: np.ndarray, lego_palette: np.ndarray) -> np.ndarray:
  from skimage import color

  scaled = rgb_array.astype(np.float32) / 255.0

  # 2) Reshape to (N,1,3) so that rgb2lab sees it as an image of height=N, width=1, channels=3
  reshaped = scaled.reshape((-1, 1, 3))

  # 3) Convert to Lab
  lab_reshaped = rgb2lab(reshaped)  # shape: (N,1,3)

  # 4) Reshape back to (N,3)
  lab_array = lab_reshaped.reshape((-1, 3))

def find_nearest_lego_colors_lab_weighted(
    lab_colors: np.ndarray,
    lego_palette_lab: np.ndarray,
    lego_palette_names: list,
    lightness_weight: float = 0.2
) -> np.ndarray:
    """
    Find the nearest LEGO color in Lab space for each input Lab color,
    reducing the influence of Lightness (L) in the distance calculation.

    Args:
        lab_colors (np.ndarray): (N,3) array of Lab colors (input colors).
        lego_palette_lab (np.ndarray): (M,3) array of Lab colors (LEGO palette colors).
        lego_palette_names (list): List of M names corresponding to the LEGO colors.
        lightness_weight (float): Weight for the L (lightness) component in the distance calculation.

    Returns:
        np.ndarray: (N,) array of LEGO color names corresponding to the closest match for each input color.
    """
    # Expand lab_colors to (N,1,3) and lego_palette_lab to (1,M,3)
    lab_colors_exp = lab_colors[:, np.newaxis, :]  # (N,1,3)
    lego_palette_exp = lego_palette_lab[np.newaxis, :, :]  # (1,M,3)

    # Apply weights: Scale L component
    lab_colors_exp[:, :, 0] *= lightness_weight
    lego_palette_exp[:, :, 0] *= lightness_weight

    # Compute weighted Euclidean distance in Lab space (L2 Norm) across the last axis
    distances = np.linalg.norm(lab_colors_exp - lego_palette_exp, axis=2)  # (N,M)

    # Find the index of the minimum distance for each row
    closest_indices = np.argmin(distances, axis=1)  # (N,)

    # Map indices to LEGO color names
    closest_colors = np.array([lego_palette_names[i] for i in closest_indices])

    return closest_colors


# Should I merge colors first or colors and bits at the same time?
def to_df(voxels, colors) -> pl.DataFrame:
  df = pl.from_numpy(voxels.sparse_indices, schema=["x", "z", "y"])
  df = df.with_columns(color=pl.Series(colors))
  return df


In [ ]:
df

In [ ]:
np.unique(np.asarray(mid_colors), axis=0).shape,np.unique(np.asarray(colors)[:,:3], axis=0).shape

In [197]:
# This merges color while walking along neighbors. It's suboptimal in that it might override a previous group with a new neighbour. Should include visited.
if False:
  import pandas as pd
  from scipy.spatial.distance import cdist
  def get_neighbors(x, y, z):
      """6-connected neighbors in 3D."""
      return [
          (x+1, y, z), (x-1, y, z),
          (x, y+1, z), (x, y-1, z),
          (x, y, z+1), (x, y, z-1)
      ]

  def coord_to_idx(df: pl.DataFrame) -> dict[tuple[int,int,int], int]:
    return dict(zip(zip(df["x"], df["y"], df["z"]), range(len(df))))

  df = df.drop("r", "b", "g", strict=False).with_columns(colors=pl.Series(colors))
  coord_to_idx = coord_to_idx(df)
  groups = {}
  df = df.with_columns(group=pl.arange(pl.len()))
  color_np = df["color"].to_numpy()
  color_diff = cdist(color_np, color_np, 'euclidean') # indexed diff

  for idx in range(len(df)):
    neighbors = get_neighbors(df[idx, "x"], df[idx, "y"], df[idx, "z"])
    for neighbor in neighbors:
      if neighbor in coord_to_idx:
        neighbor_idx = coord_to_idx[neighbor]
        if neighbor_idx < idx:
          continue
        if (color_diff[idx, neighbor_idx] < 50):
          df[neighbor_idx, "group"] = df[idx, "group"] # bad mutation...

  color_list = pl.col("color").arr
  df_group_color = df.with_columns(r=color_list.get(0), b=color_list.get(1), g=color_list.get(2)).group_by("group").agg(pl.mean("r", "g", "b"))
  df = df.join(df_group_color, on="group")
  df.head()
  df = df.with_columns(color_rgb=pl.concat_str("r", "b", "g", separator=",")).with_columns(
      color_rgb = "rgb("+pl.col("color_rgb")+")"
  )
  display_voxels_px(voxels, df["color_rgb"])

In [ ]:
mid_colors = [normalize_value_to_mid(x, 0.8) for x in colors]
display_voxels_px(voxels, [f"rgb{c[0],c[1],c[2]}" for c in mid_colors])

In [ ]:
# map_colors_to_lego, map_color_cie, quantize_colors, convert_colors_max_diff
color_lego = map_color_cie(np.asarray(mid_colors)[:,:3], np.asarray(LEGO_COLORS_RGB))
display_voxels_px(voxels, [f"rgb{c[0],c[1],c[2]}" for c in color_lego])

In [ ]:
color_lego = quantize_colors(np.asarray(mid_colors)[:,:3], k=16)
display_voxels_px(voxels, [f"rgb{c[0],c[1],c[2]}" for c in color_lego])

In [ ]:
display_voxels_px(voxels, [f"rgb{c[0],c[1],c[2]}" for c in colors])

In [202]:
df = to_df(voxels, color_lego)

In [ ]:
df

In [204]:
BLOCK_SIZES = np.asarray([
    [1,1],[1,2],[1,3],[1,4],[1,6],[1,8],
    [2,2],[2,3],[2,4],[2,6],[2,8]
])
coords = {(x,y,z) for x,y,z in df.select("x", "y", "z").to_numpy()}

In [ ]:
# TODO: make sure user flips figure to stand on z = 0, z being height axis.

def get_xy_neighbors(x, y, z):
  return [(x-1,y,z), (x+1,y,z), (x, y-1,z), (x,y+1,z)]

y_group_1 = df.filter((pl.col("z") == 16) & (pl.col("color") == [44, 94, 130]))
group_coords = {(x,y,z) for x,y,z in y_group_1[["x", "y", "z"]].to_numpy()}

for row in range(len(y_group_1)):
  for neighbor in get_xy_neighbors(y_group_1[row, "x"], y_group_1[row, "y"], y_group_1[row, "z"]):
    if neighbor in group_coords:
      "found"

In [ ]:
def merge_into_bricks(grouped_df: pl.DataFrame) -> pl.DataFrame:
    color_str = grouped_df[0,"color_str"]
    z_val = grouped_df[0, "z"]

    xy_grid = np.zeros((grouped_df["x"].max() + 1, grouped_df["y"].max() +1), dtype=bool)
    xy_grid[grouped_df["x"], grouped_df["y"]] = 1
    out_rows = []
    grouped_df = grouped_df.sort(by=["x", "y"])
    coords = {(x,y) for x,y in grouped_df[["x", "y"]].to_numpy()}

    while coords:
        (x0, y0) = coords.pop()
        coords.add((x0, y0))  # reinsert until placed

        placed = False
        for (width, height) in BLOCK_SIZES:
            if x0+width > xy_grid.shape[0] or y0+height > xy_grid.shape[1]:
                continue
            if np.all(xy_grid[x0:x0+width, y0:y0+height] == 1):
                place_block(x0, y0, width, height, coords)
                out_rows.append((color_str, z_val, x0, y0, width, height))
                placed = True
                break

        if not placed:
            # fallback to 1x1
            coords.remove((x0, y0))
            out_rows.append((color_str, z_val, x0, y0, 1, 1))

    return pl.DataFrame(
        {
            "color_str": [row[0] for row in out_rows],
            "z":         [row[1] for row in out_rows],
            "x":         [row[2] for row in out_rows],
            "y":         [row[3] for row in out_rows],
            "width":     [row[4] for row in out_rows],
            "height":    [row[5] for row in out_rows],
        }
    )

def can_place_block(x0, y0, w, h, coords):
    for xx in range(x0, x0 + w):
        for yy in range(y0, y0 + h):
            if (xx, yy) not in coords:
                return False
    return True

def place_block(x0, y0, w, h, coords):
    for xx in range(x0, x0 + w):
        for yy in range(y0, y0 + h):
            coords.remove((xx, yy))

In [ ]:
def merge_cells_recursive(df_group: pl.DataFrame, coords: set[tuple[int, int, int]]) -> pl.DataFrame:
  # Merge by xy_grid as above.

  pass


def merge_cells(df_group: pl.DataFrame, coords: set[tuple[int, int, int]]) -> pl.DataFrame:
  # df [x, y, z, x2, y2, z2, color] (merged)
  # df [x, y, z, color] (unmerged)
  pass

BLOCK_SIZES = [
    [1,1],[1,2],[1,3],[1,4],[1,6],[1,8],
    [2,1],[3,1],[4,1],[6,1],[8,1],
    [2,2],[2,3],[2,4],[2,6],[2,8],
    [3,2],[4,2],[6,2],[8,2]
]
# Sort array by area, largest first.
BLOCK_SIZES.sort(key=lambda x: x[0]*x[1], reverse=True)

coords = {(x,y,z) for x,y,z in df.select("x", "y", "z").to_numpy()}
# Colors already merged.
df = df.with_columns(color_str = pl.col("color").cast(pl.List(pl.String)).list.join("_"))
merge_into_bricks(df.filter(pl.col("z") == 17))
(df
 .group_by("color_str", "z")
 .map_groups(merge_into_bricks)
 .select(w_h=pl.struct("width", "height").value_counts()).unnest("w_h")
)



## Utils

### Enhance Brightness, Gamma and Saturation (color)

In [ ]:
def enhance_mesh_colors_vectorized(mesh, saturation_boost=1.5, brightness_factor=1.2, gamma=1.8):
    """
    Enhances the saturation, brightness, and optionally applies gamma correction to mesh colors (vectorized).

    Args:
        mesh: The trimesh mesh object.
        saturation_boost: Factor to boost saturation ( > 1 increases saturation).
        brightness_factor: Factor to adjust brightness ( > 1 increases brightness).
        gamma: Gamma value for gamma correction (typically between 1.8 and 2.2).
    """
    # Convert RGB to HSV (vectorized)
    colors = mesh.visual.vertex_colors.astype(np.float32) / 255.0  # Normalize to 0-1
    hsv_colors = np.array([colorsys.rgb_to_hsv(r, g, b) for r, g, b, a in colors])

    # Boost saturation (vectorized)
    hsv_colors[:, 1] = np.minimum(hsv_colors[:, 1] * saturation_boost, 1.0)

    # Adjust brightness (vectorized)
    hsv_colors[:, 2] = np.minimum(hsv_colors[:, 2] * brightness_factor, 1.0)

    # Gamma correction (vectorized)
    hsv_colors[:, 2] = hsv_colors[:, 2]**(1/gamma)

    # Convert back to RGB (vectorized)
    rgb_colors = np.array([colorsys.hsv_to_rgb(h, s, v) for h, s, v in hsv_colors])

    # Add alpha channel back
    rgb_colors = np.concatenate((rgb_colors, colors[:, 3:]), axis=1)

    # Denormalize and set back to mesh
    mesh = mesh.copy()
    mesh.visual.vertex_colors = (rgb_colors * 255).astype(np.uint8)
    return mesh

# ... (load mesh)

# Enhance colors (vectorized)
enhance_mesh_colors_vectorized(mesh, saturation_boost=1.8, brightness_factor=1.2, gamma=2.0).show()

### Show RGB

In [ ]:
from IPython.display import display, HTML
def show_rgb(rgb_color):
  html_code = f'<div style="background-color: rgb{rgb_color}; width: 100px; height: 100px;"></div>'

  display(HTML(html_code))

### Validate Points similar

In [ ]:
import plotly.graph_objects as go
import numpy as np
def validate_points_similar(index: int):
  """N.B. Uses attributes available in notebook!"""
  # Create Plotly figure
  fig = go.Figure(data=[
      go.Mesh3d(
          x=mesh.vertices[:, 0],
          y=mesh.vertices[:, 1],
          z=mesh.vertices[:, 2],
          i=mesh.faces[:, 0],
          j=mesh.faces[:, 1],
          k=mesh.faces[:, 2],
          color='lightgray',
          opacity=0.8
      ),
      go.Scatter3d(
          x=mesh.vertices[vertex_indices[index:index+1], 0],
          y=mesh.vertices[vertex_indices[index:index+1], 1],
          z=mesh.vertices[vertex_indices[index:index+1], 2],
          mode='markers',
          marker=dict(size=5, color='red'),
          name='Mesh Vertex'
      ),
      go.Scatter3d(
          x=[voxels.points[index, 0]],
          y=[voxels.points[index, 1]],
          z=[voxels.points[index, 2]],
          mode='markers',
          marker=dict(size=5, color='blue'),
          name='Voxel Point'
      )
  ])

  # Set layout (axis labels, title)
  fig.update_layout(
      scene=dict(
          xaxis_title='X',
          yaxis_title='Y',
          zaxis_title='Z'
      ),
      title='Mesh with Two Corresponding Points'
  )

  # Enable interactive mode for Colab
  fig.show(renderer="colab")

In [ ]:
validate_points_similar(200)